In [1]:
import os 
wd = os.path.dirname(os.getcwd()).replace('\\', '/')
os.chdir(wd)

import folium 
import pandas as pd
import geopandas as gpd
import scripts.preprocess_helper as ph
import scripts.cleanup_helper as ch
import omegaconf
import warnings
from branca.element import Figure, MacroElement

warnings.filterwarnings('ignore')
pd.set_option('display.max_columns', None)

In [2]:
yaml_path = os.path.join(wd, 'conf', 'config.yaml').replace('\\', '/')
cfg = omegaconf.OmegaConf.load(yaml_path)
paths = cfg.paths

In [37]:
#Set the paths to the data
rural_coops_path = os.path.join(wd, paths.utilities.rural_coops_path).replace('\\', '/')
municipal_utils_path = os.path.join(wd, paths.utilities.municipal_utils_path).replace('\\', '/')

cty_borders_path = os.path.join(wd, paths.boundaries.ct_clean_path).replace('\\', '/')
st_borders_path = os.path.join(wd, paths.boundaries.st_clean_path).replace('\\', '/')

j40_path = os.path.join(wd, paths.j40.j40_clean_path).replace('\\', '/')
coal_path = os.path.join(wd, paths.energy.coal_clean_path).replace('\\', '/')
ffe_path = os.path.join(wd, paths.energy.ffe_clean_path).replace('\\', '/')
lic_path = os.path.join(wd, paths.low_income.low_inc_clean_path).replace('\\', '/')

op_path = os.path.join(wd, 'results').replace('\\', '/')
j40_coop_op_path = os.path.join(op_path, 'j40','coop').replace('\\', '/')
j40_mun_op_path = os.path.join(op_path, 'j40','mun').replace('\\', '/')
coal_coop_op_path = os.path.join(op_path, 'coal','coop').replace('\\', '/')
coal_mun_op_path = os.path.join(op_path, 'coal','mun').replace('\\', '/')
ffe_coop_op_path = os.path.join(op_path, 'ffe','coop').replace('\\', '/')
ffe_mun_op_path = os.path.join(op_path, 'ffe','mun').replace('\\', '/')
lic_coop_op_path = os.path.join(op_path, 'lic','coop').replace('\\', '/')
lic_mun_op_path = os.path.join(op_path, 'lic','mun').replace('\\', '/')

states_path = os.path.join(wd, paths.boundaries.state_fips_path).replace('\\', '/')

In [26]:
%%time
#Read in data
rural_coops = gpd.read_file(rural_coops_path).to_crs("EPSG:3857")
municipal_utils = gpd.read_file(municipal_utils_path).to_crs("EPSG:3857")
j40 = gpd.read_file(j40_path).to_crs("EPSG:3857")
coal = gpd.read_file(coal_path).to_crs("EPSG:3857")
ffe = gpd.read_file(ffe_path).to_crs("EPSG:3857")
low_inc = gpd.read_file(lic_path).to_crs("EPSG:3857")
cty_borders = gpd.read_file(cty_borders_path).to_crs("EPSG:3857")
state_borders = gpd.read_file(st_borders_path).to_crs("EPSG:3857")
state_df = pd.read_csv(states_path)

CPU times: total: 0 ns
Wall time: 43 ms


In [6]:
%%time
## Make the overlays of each community separately with rural and municipal utilities
from scripts.overlays import overlays, save_overlays

j40_coop_overlays = overlays('j40', rural_coops, j40) #Justice40 - Rural
j40_mun_overlays = overlays('j40', municipal_utils, j40) #Justice40 - Municipal
coal_coop_overlays = overlays('coal', rural_coops, coal) #Coal - Rural
coal_mun_overlays = overlays('coal', municipal_utils, coal) #Coal - Municipal
ffe_coop_overlays = overlays('ffe', rural_coops, ffe) #FFE - Rural
ffe_mun_overlays = overlays('ffe', municipal_utils, ffe) #FFE - Municipal
lic_coop_overlays = overlays('low_income', rural_coops, low_inc) #Low Income - Rural
lic_mun_overlays = overlays('low_income', municipal_utils, low_inc) #Low Income - Municipal


CPU times: total: 2min 55s
Wall time: 8min 2s


In [50]:
#Take only the columns we need
j40_coop_overlays = j40_coop_overlays[['NAME', 'Type_1', 'Type', 'State_1', 'County','perc_cover','geometry']]
j40_mun_overlays = j40_mun_overlays[['NAME', 'Type_1', 'Type', 'State_1', 'County','perc_cover','geometry']]
coal_coop_overlays = coal_coop_overlays[['NAME', 'Type_1', 'Type', 'Subtype', 'State_1', 'County','perc_cover','geometry']]
coal_mun_overlays = coal_mun_overlays[['NAME', 'Type_1', 'Type', 'Subtype', 'State_1', 'County','perc_cover','geometry']]
ffe_coop_overlays = ffe_coop_overlays[['NAME', 'Type_1', 'Type', 'MSA_NMSA', 'State_1', 'County','perc_cover','geometry']]
ffe_mun_overlays = ffe_mun_overlays[['NAME', 'Type_1', 'Type', 'MSA_NMSA', 'State_1', 'County','perc_cover','geometry']]
lic_coop_overlays = lic_coop_overlays[['NAME', 'Type_1', 'Type', 'State','perc_cover','geometry']]
lic_mun_overlays = lic_mun_overlays[['NAME', 'Type_1', 'Type', 'State','perc_cover','geometry']]
lic_coop_overlays.rename(columns={'State':'State_1'}, inplace=True)
lic_mun_overlays.rename(columns={'State':'State_1'}, inplace=True)

In [19]:
##Folium test
fig = Figure(width=800,height=700)
m = folium.Map(location=[39.8283, -89.5795], zoom_start=7, control_scale=True)#tiles='openstreetmap', 

j40_test = j40_coop_overlays[j40_coop_overlays['State_1']== "Illinois"]
choropleth_layer = folium.Choropleth(
    geo_data=j40_test,
    data=j40_test,
    columns=['NAME','perc_cover'],
    key_on='feature.properties.NAME',
    fill_color='YlGn'
).add_to(m)

# Add tooltips to the choropleth layer
tooltip = folium.GeoJsonTooltip(
    fields=['NAME', 'perc_cover'],  # The fields to display in the tooltip
    aliases=['CoOp Name', 'Area Covered by J40'],  # The tooltip field aliases
    localize=True  # Format numbers with commas and periods based on the browser locale
)
choropleth_layer.geojson.add_child(tooltip)

m

In [77]:
def generate_maps(df:gpd.GeoDataFrame,state:str, op_path:str, community:str,util_type:str):
    fig = Figure(width=800,height=700)
    m = folium.Map(location=[39.8283, -89.5795], zoom_start=4, control_scale=True)#tiles='openstreetmap', 
    df = df[df['State_1']== state]
    choropleth_layer = folium.Choropleth(
        geo_data=df,
        data=df,
        columns=['NAME','perc_cover'],
        key_on='feature.properties.NAME',
        fill_color='YlGn'
    ).add_to(m)
    if util_type == 'coop':
        # Add tooltips to the choropleth layer
        tooltip = folium.GeoJsonTooltip(
            fields=['NAME', 'perc_cover'],  # The fields to display in the tooltip
            aliases=['Coop Name', 'Percenatge Area Covered by The community'],  # The tooltip field aliases
            localize=True  # Format numbers with commas and periods based on the browser locale
        )
    elif util_type == 'municipal':
        tooltip = folium.GeoJsonTooltip(
            fields=['NAME', 'perc_cover'],  # The fields to display in the tooltip
            aliases=['Municipal Utility Name', 'Percenatge Area Covered by The community'],  # The tooltip field aliases
            localize=True  # Format numbers with commas and periods based on the browser locale
        )
    choropleth_layer.geojson.add_child(tooltip)
    fig.add_child(m)
    save_path = os.path.join(op_path, util_type,community).replace('\\', '/')
    os.makedirs(save_path, exist_ok=True)
    fig.save(os.path.join(save_path ,f'{state}_{community}.html'))

In [73]:
rural_overlays = [j40_coop_overlays, coal_coop_overlays, ffe_coop_overlays, lic_coop_overlays]
mun_overlays = [j40_mun_overlays, coal_mun_overlays, ffe_mun_overlays, lic_mun_overlays]
communities = ['j40','coal','ffe','lic']
# states = list(state_df.State.unique())

In [78]:
%%time
#Generate maps for each community on a state level and save them as html files for Illinois state for the coops
for community in communities:
    for overlay in rural_overlays:
        generate_maps(df = overlay, state = 'Illinois', op_path=op_path, community = community, util_type ='coop')

CPU times: total: 40 s
Wall time: 41.7 s


In [79]:
%%time
#Generate maps for each community on a state level and save them as html files for Illinois state for the coops
for community in communities:
    for overlay in mun_overlays:
        generate_maps(df = overlay, state = 'Illinois', op_path=op_path, community = community, util_type ='municipal')

CPU times: total: 58.2 s
Wall time: 1min 4s
